
<div style="text-align: center; line-height: 0; padding-top: 9px;">
  <img src="https://databricks.com/wp-content/uploads/2018/03/db-academy-rgb-1200px.png" alt="Databricks Learning">
</div>



# Lab: Preparing Data for RAG

The objective of this lab is to demonstrate the process of ingesting and processing documents for a Retrieval-Augmented Generation (RAG) application. This involves extracting text from PDF documents, computing embeddings using a foundation model, and storing the embeddings in a Delta table.


**Lab Outline:**

In this lab, you will need to complete the following tasks:

* **Task 1 :** Read the PDF files and load them into a DataFrame.

* **Task 2 :** Extract the text content from the PDFs and split it into manageable chunks.

* **Task 3 :** Compute embeddings for each text chunk using a foundation model endpoint.

* **Task 4 :** Create a Delta table to store the computed embeddings.

**📝 Your task:** Complete the **`<FILL_IN>`** sections in the code blocks and follow the other steps as instructed.

## REQUIRED - SELECT CLASSIC COMPUTE
Before executing cells in this notebook, please select your classic compute cluster in the lab. Be aware that **Serverless** is enabled by default.

Follow these steps to select the classic compute cluster:
1. Navigate to the top-right of this notebook and click the drop-down menu to select your cluster. By default, the notebook will use **Serverless**.

2. If your cluster is available, select it and continue to the next cell. If the cluster is not shown:

   - Click **More** in the drop-down.
   
   - In the **Attach to an existing compute resource** window, use the first drop-down to select your unique cluster.

**NOTE:** If your cluster has terminated, you might need to restart it in order to select it. To do this:

1. Right-click on **Compute** in the left navigation pane and select *Open in new tab*.

2. Find the triangle icon to the right of your compute cluster name and click it.

3. Wait a few minutes for the cluster to start.

4. Once the cluster is running, complete the steps above to select your cluster.

## Requirements

Please review the following requirements before starting the lesson:

* To run this notebook, you need to use one of the following Databricks runtime(s): **15.4.x-cpu-ml-scala2.12**


## Classroom Setup

Before starting the lab, run the provided classroom setup script. This script will define configuration variables necessary for the lab. Execute the following cell:

In [0]:
%pip install -qq -U llama-index pydantic PyPDF2
dbutils.library.restartPython()

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
langchain 0.1.20 requires tenacity<9.0.0,>=8.1.0, but you have tenacity 9.1.2 which is incompatible.
langchain-community 0.0.38 requires tenacity<9.0.0,>=8.1.0, but you have tenacity 9.1.2 which is incompatible.
langchain-core 0.1.52 requires tenacity<9.0.0,>=8.1.0, but you have tenacity 9.1.2 which is incompatible.
ydata-profiling 4.5.1 requires pydantic<2,>=1.8.1, but you have pydantic 2.11.7 which is incompatible.
virtualenv 20.24.2 requires platformdirs<4,>=3.9.1, but you have platformdirs 4.3.8 which is incompatible.
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
%run ../Includes/Classroom-Setup-02

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.



The examples and models presented in this course are intended solely for demonstration and educational purposes.
 Please note that the models and prompt examples may sometimes contain offensive, inaccurate, biased, or harmful content.


**Other Conventions:**

Throughout this demo, we'll refer to the object `DA`. This object, provided by Databricks Academy, contains variables such as your username, catalog name, schema name, working directory, and dataset locations. Run the code block below to view these details:

In [0]:
print(f"Username:          {DA.username}")
print(f"Catalog Name:      {DA.catalog_name}")
print(f"Schema Name:       {DA.schema_name}")
print(f"Working Directory: {DA.paths.working_dir}")
print(f"Dataset Location:  {DA.paths.datasets}")

Username:          labuser11131632_1754970105@vocareum.com
Catalog Name:      dbacademy
Schema Name:       labuser11131632_1754970105
Working Directory: /Volumes/dbacademy/ops/labuser11131632_1754970105@vocareum_com
Dataset Location:  NestedNamespace (arxiv='/Volumes/dbacademy_arxiv/v01', dais='/Volumes/dbacademy_dais/v01', news='/Volumes/dbacademy_news/v01', docs='/Volumes/dbacademy_docs/v01')


## Task 1: Read the PDF files and load them into a DataFrame.

To start, you need to load the PDF files into a DataFrame.

**Steps:**

1. Use Spark to load the binary PDFs into a DataFrame.

2. Ensure that each PDF file is represented as a separate record in the DataFrame.

In [0]:
## run this cell to import the required libraries
from llama_index.core.node_parser import SentenceSplitter
from llama_index.core.schema import Document
from llama_index.core.utils import set_global_tokenizer
from transformers import AutoTokenizer
from typing import Iterator
from pyspark.sql.functions import col, udf, length, pandas_udf, explode
import os
import pandas as pd 
import io
from PyPDF2 import PdfReader

In [0]:
## use Spark to load the PDF files into a DataFrame
## reduce the arrow batch size as our PDF can be big in memory
spark.conf.set("spark.sql.execution.arrow.maxRecordsPerBatch", 10)
articles_path = f"{DA.paths.datasets.arxiv}/arxiv-articles/"
table_name = f"{DA.catalog_name}.{DA.schema_name}.lab_pdf_raw_text"

## read pdf files
df = (
        spark.read.format("binaryfile")
        .option("recursiveFileLookup", "true")
        .load(articles_path)
        )

## save list of the files to table
df.write.mode("overwrite").saveAsTable(table_name)

display(df)

path modificationTime length content dbfs:/Volumes/dbacademy_arxiv/v01/arxiv-articles/2204.01691.pdf 2024-11-13T03:33:23Z 12827088 JVBERi0xLjUKJY8KMTI5IDAgb2JqCjw8IC9UeXBlIC9YT2JqZWN0IC9TdWJ0eXBlIC9JbWFnZSAvQml0c1BlckNvbXBvbmVudCA4Ci9Db2xvclNwYWNlIC9EZXZpY2VSR0IgL0ZpbHRlciAvRmxhdGVEZWNvZGUgL0hlaWdodCA= (truncated) dbfs:/Volumes/dbacademy_arxiv/v01/arxiv-articles/2311.15732.pdf 2024-11-13T03:33:27Z 7811582 JVBERi0xLjUKJY8KMTQ1IDAgb2JqCjw8IC9GaWx0ZXIgL0ZsYXRlRGVjb2RlIC9MZW5ndGggMzkxMyA+PgpzdHJlYW0KeNqtWllz3DYSfvevmJet5VRpKIIAL7/ZsZ31lrxxbK1TtbEfMBxohmsOyfCwovz67QPkkCMoZUVbLos= (truncated) dbfs:/Volumes/dbacademy_arxiv/v01/arxiv-articles/2302.09419.pdf 2024-11-13T03:33:26Z 5825471 JVBERi0xLjUKJY8KMzA4IDAgb2JqCjw8IC9GaWx0ZXIgL0ZsYXRlRGVjb2RlIC9MZW5ndGggMjgwMSA+PgpzdHJlYW0KeNq1WUmX2zYSvvev4JGaZ3FIcAE5p9ideBs7Y7t73mRxDmgKkjCmSJmLO/avn69QoESp2XE7b3IRgUI= (truncated) dbfs:/Volumes/dbacademy_arxiv/v01/arxiv-articles/2209.07753.pdf 2024-11-13T03:33:24Z 3200561 JVBERi0xLjUKJY8KMTU0IDAgb2JqCjw8IC9UeXBlIC9YT2JqZWN0IC9TdWJ0eXBlIC9Gb3JtIC9CQm94IFsgMCAwIDQ5MyAzMjEgXQovRmlsdGVyIC9GbGF0ZURlY29kZSAvRm9ybVR5cGUgMSAvR3JvdXAgMTY4IDAgUiAvTGU= (truncated) dbfs:/Volumes/dbacademy_arxiv/v01/arxiv-articles/2303.04671.pdf 2024-11-13T03:33:26Z 2452715 JVBERi0xLjUKJY8KMTEgMCBvYmoKPDwgL1R5cGUgL1hPYmplY3QgL1N1YnR5cGUgL0Zvcm0gL0JCb3ggWyAwIDAgNDk3LjQgMzkxLjA4IF0KL0ZpbHRlciAvRmxhdGVEZWNvZGUgL0Zvcm1UeXBlIDEgL0dyb3VwIDI0IDAgUiA= (truncated) dbfs:/Volumes/dbacademy_arxiv/v01/arxiv-articles/2303.10130.pdf 2024-11-13T03:33:26Z 2119311 JVBERi0xLjUKJY8KMTc5IDAgb2JqCjw8IC9GaWx0ZXIgL0ZsYXRlRGVjb2RlIC9MZW5ndGggMjU2MCA+PgpzdHJlYW0KeNqdWEl33LgRvutX8BYyz6IBgmt8sl9sxzOTscdWng/jOaC7ITVtLj1cJMu/PrWBpFrKHHIiWCgUCrU= (truncated) dbfs:/Volumes/dbacademy_arxiv/v01/arxiv-articles/2203.02155.pdf 2024-11-13T03:33:22Z 1797405 JVBERi0xLjUKJY8KMjQ1IDAgb2JqCjw8IC9GaWx0ZXIgL0ZsYXRlRGVjb2RlIC9MZW5ndGggMjcxOCA+PgpzdHJlYW0KeNqdWVlz20YSftevwNuCVSKCuXA4Lytr48SOvNHaqtqtTfIwIoYkIhDg4rCsf7/d0w0QPGyn8iIOeq4= (truncated) dbfs:/Volumes/dbacademy_arxiv/v01/arxiv-articles/2302.06476.pdf 2024-11-13T03:33:25Z 1051746 JVBERi0xLjUKJY8KNjcgMCBvYmoKPDwgL0ZpbHRlciAvRmxhdGVEZWNvZGUgL0xlbmd0aCAyNzQ3ID4+CnN0cmVhbQp42rUZ2ZLbxvF9v4JvAasWo7lw+UWl2JbjWJIVa1Opip0HLDlLogQCNACaWn99uqd7SABLeiWnUlItZno= (truncated) dbfs:/Volumes/dbacademy_arxiv/v01/arxiv-articles/2403.06254.pdf 2024-11-13T03:33:27Z 568961 JVBERi0xLjUKJY8KNSAwIG9iago8PCAvRmlsdGVyIC9GbGF0ZURlY29kZSAvTGVuZ3RoIDU4NiA+PgpzdHJlYW0KeNptVMuO4jAQvOcrvAck5sDgByQwipAgD4nDDqMBrfYKiWEjQRIl4cDfr6ubwMxqD0TV5bK7q+1m8ONjO1o= (truncated) dbfs:/Volumes/dbacademy_arxiv/v01/arxiv-articles/2302.07842.pdf 2024-11-13T03:33:25Z 533444 JVBERi0xLjQKJcfsj6IKNSAwIG9iago8PC9MZW5ndGggNiAwIFIvRmlsdGVyIC9GbGF0ZURlY29kZT4+CnN0cmVhbQp4nO1cXXMdx3FNVd7wG/RwH+9N+a7m+8NPkWg5oUuKJQUpJSX7ASRAkCIJ0iCBSP7FTlV+RE7Pzuz07M4= (truncated)

## Task 2: Extract the text content from the PDFs and split it into manageable chunks

Next, extract the text content from the PDFs and split it into manageable chunks.

**Steps:**

1. Define a function to split the text content into chunks.

    * Split the text content into manageable chunks.

    * Ensure each chunk contains a reasonable amount of text for processing.

2. Apply the function to the DataFrame to create a new DataFrame with the text chunks.


In [0]:
## Define a function to split the text content into chunks
@pandas_udf("array<string>")
def read_as_chunk(batch_iter: Iterator[pd.Series]) -> Iterator[pd.Series]:
    ## Set llama2 as tokenizer
    set_global_tokenizer(
      AutoTokenizer.from_pretrained("hf-internal-testing/llama-tokenizer")
    )
    ## Sentence splitter from llama_index to split on sentences
    splitter = SentenceSplitter(chunk_size=500, chunk_overlap=50)
    
    def extract_and_split(b):
        txt = parse_bytes_pypdf(b)
        if txt is None:
            return []
        nodes = splitter.get_nodes_from_documents([Document(text=txt)])
        return [n.text for n in nodes]

    for x in batch_iter:
        yield x.apply(extract_and_split)

df_chunks = (df
              .withColumn("content", explode(read_as_chunk("content")))
              .selectExpr("path as pdf_name", "content")
            )
display(df_chunks)

pdf_name content dbfs:/Volumes/dbacademy_arxiv/v01/arxiv-articles/2204.01691.pdf Do As I Can, Not As I Say:
Grounding Language in Robotic Affordances
1Michael Ahn, Anthony Brohan, Noah Brown, Yevgen Chebotar, Omar Cortes, Byron David,
Chelsea Finn, Chuyuan Fuy, Keerthana Gopalakrishnan, Karol Hausman, Alex Herzogy,
Daniel Hoy, Jasmine Hsu, Julian Ibarz, Brian Ichter, Alex Irpan, Eric Jang,
Rosario Jauregui Ruano, Kyle Jeffrey, Sally Jesmonth, Nikhil J Joshi, Ryan Julian,
Dmitry Kalashnikov, Yuheng Kuang, Kuang-Huei Lee, Sergey Levine, Yao Lu, Linda Luu,
Carolina Parada, Peter Pastory, Jornell Quiambao, Kanishka Rao, Jarek Rettinghouse,
Diego Reyes, Pierre Sermanet, Nicolas Sievers, Clayton Tan, Alexander Toshev,
Vincent Vanhoucke, Fei Xia, Ted Xiao, Peng Xu, Sichun Xu, Mengyuan Yany, Andy Zeng
Robotics at Google,yEveryday Robots
Abstract: Large language models can encode a wealth of semantic knowledge
about the world. Such knowledge could be extremely useful to robots aiming to act
upon high-level, temporally extended instructions expressed in natural language.
However, a signiﬁcant weakness of language models is that they lack real-world
experience, which makes it difﬁcult to leverage them for decision making within
a given embodiment. For example, asking a language model to describe how to
clean a spill might result in a reasonable narrative, but it may not be applicable to
a particular agent, such as a robot, that needs to perform this task in a particular
environment. dbfs:/Volumes/dbacademy_arxiv/v01/arxiv-articles/2204.01691.pdf We propose to provide real-world grounding by means of pretrained
skills, which are used to constrain the model to propose natural language actions
that are both feasible and contextually appropriate. The robot can act as the lan-
guage model’s “hands and eyes,” while the language model supplies high-level
semantic knowledge about the task. We show how low-level skills can be com-
bined with large language models so that the language model provides high-level
knowledge about the procedures for performing complex and temporally extended
instructions, while value functions associated with these skills provide the ground-
ing necessary to connect this knowledge to a particular physical environment. We
evaluate our method on a number of real-world robotic tasks, where we show
the need for real-world grounding and that this approach is capable of complet-
ing long-horizon, abstract, natural language instructions on a mobile manipulator.
The project’s website, the video, and open sourced code in a tabletop domain can
be found at say-can.github.io .
Figure 1: LLMs have not interacted with their environment and observed the outcome of their responses, and
thus are not grounded in the world. SayCan grounds LLMs via value functions of pretrained skills, allowing
them to execute real-world, abstract, long-horizon commands on robots.
1 Introduction
Recent progress in training large language models (LLMs) has led to systems that can generate
complex text based on prompts, answer questions, or even engage in dialogue on a wide range of
topics. These models absorb vast quantities of knowledge from text corpora mined from the web,
1Authors listed in alphabetical order. dbfs:/Volumes/dbacademy_arxiv/v01/arxiv-articles/2204.01691.pdf These models absorb vast quantities of knowledge from text corpora mined from the web,
1Authors listed in alphabetical order. Contributions in Appendix B.
Corresponding emails: fichter,xiafei,karolhausman g@google.com .arXiv:2204.01691v2 [cs.RO] 16 Aug 2022
and we might wonder whether knowledge of everyday tasks that is encoded in such models can be
used by robots to perform complex tasks in the real world. But how can embodied agents extract
and harness the knowledge of LLMs for physically grounded tasks?
This question poses a major challenge. LLMs are not grounded in the physical world and they
do not observe the consequences of their generat

## Task 3: Compute embeddings for each text chunk using a foundation model endpoint
Now, compute embeddings for each text chunk using a foundation model endpoint.

**Steps:**

1. Define a function to compute embeddings for text chunks.
    + Use a foundation model endpoint to compute embeddings for each text chunk.
    + Ensure that the embeddings are computed efficiently, considering the limitations of the model.  

2. Apply the function to the DataFrame containing the text chunks to compute embeddings for each chunk.


In [0]:
## define a function to compute embeddings for text chunks
@pandas_udf("array<float>")
def get_embedding(contents: pd.Series) -> pd.Series:
    import mlflow.deployments
    deploy_client = mlflow.deployments.get_deploy_client("databricks")
    
    def get_embeddings(batch):
        ## calculate embeddings using the deployment client's predict function 
        ## NOTE: this will fail if an exception is thrown during embedding creation (add try/except if needed) 
        response = deploy_client.predict(endpoint="databricks-gte-large-en", inputs={"input": batch})
        return [e["embedding"] for e in response.data]

    ## splitting the contents into batches of 150 items each, since the embedding model takes at most 150 inputs per request.
    max_batch_size = 150
    batches = [contents.iloc[i:i + max_batch_size] for i in range(0, len(contents), max_batch_size)]

    ## process each batch and collect the results
    all_embeddings = []
    for batch in batches:
        all_embeddings += get_embeddings(batch.tolist())

    return pd.Series(all_embeddings)
    
df_chunk_emd = (df_chunks
                .withColumn("embedding", get_embedding("content"))
                .selectExpr("pdf_name", "content", "embedding")
                )
display(df_chunk_emd)

pdf_name content embedding dbfs:/Volumes/dbacademy_arxiv/v01/arxiv-articles/2204.01691.pdf Do As I Can, Not As I Say:
Grounding Language in Robotic Affordances
1Michael Ahn, Anthony Brohan, Noah Brown, Yevgen Chebotar, Omar Cortes, Byron David,
Chelsea Finn, Chuyuan Fuy, Keerthana Gopalakrishnan, Karol Hausman, Alex Herzogy,
Daniel Hoy, Jasmine Hsu, Julian Ibarz, Brian Ichter, Alex Irpan, Eric Jang,
Rosario Jauregui Ruano, Kyle Jeffrey, Sally Jesmonth, Nikhil J Joshi, Ryan Julian,
Dmitry Kalashnikov, Yuheng Kuang, Kuang-Huei Lee, Sergey Levine, Yao Lu, Linda Luu,
Carolina Parada, Peter Pastory, Jornell Quiambao, Kanishka Rao, Jarek Rettinghouse,
Diego Reyes, Pierre Sermanet, Nicolas Sievers, Clayton Tan, Alexander Toshev,
Vincent Vanhoucke, Fei Xia, Ted Xiao, Peng Xu, Sichun Xu, Mengyuan Yany, Andy Zeng
Robotics at Google,yEveryday Robots
Abstract: Large language models can encode a wealth of semantic knowledge
about the world. Such knowledge could be extremely useful to robots aiming to act
upon high-level, temporally extended instructions expressed in natural language.
However, a signiﬁcant weakness of language models is that they lack real-world
experience, which makes it difﬁcult to leverage them for decision making within
a given embodiment. For example, asking a language model to describe how to
clean a spill might result in a reasonable narrative, but it may not be applicable to
a particular agent, such as a robot, that needs to perform this task in a particular
environment. List(0.31176758, 0.24365234, -0.12426758, 0.3244629, -1.0371094, -0.55322266, 0.3359375, -0.6669922, -0.58984375, -0.21740723, -0.013977051, -0.0289917, -0.78027344, -0.5493164, -0.18652344, -0.41479492, 0.1850586, 0.63720703, 0.3947754, -0.72802734, 0.39648438, -0.47583008, 0.66064453, -1.1650391, -0.13574219, -0.97802734, 0.17248535, -0.05038452, 0.4987793, -0.085998535, 0.64453125, 1.1640625, -0.92871094, -0.14575195, 0.4633789, 0.65478516, -0.63378906, -0.80566406, -0.5444336, 0.47387695, 1.1621094, -0.15808105, 0.24951172, -0.40722656, -0.8544922, 0.39770508, 0.5229492, -0.4494629, -0.5566406, -7.3337555E-4, -1.4462891, 0.6557617, 1.8681641, 0.4921875, -0.1821289, 0.50878906, 0.41577148, -0.013656616, 0.1048584, 0.21191406, -1.1572266, 0.37597656, 0.29467773, -0.6308594, 1.2275391, 0.6303711, -1.03125, 0.3857422, -1.6259766, -0.36328125, 0.41210938, -0.63916016, 0.28198242, -0.62939453, 0.42944336, -1.0615234, -0.9916992, 0.91748047, 0.9663086, 0.016113281, -0.46801758, -1.046875, -0.59472656, -1.3701172, -0.22216797, -0.49658203, 0.47387695, -0.4387207, 0.71533203, 1.0410156, 1.0449219, -0.44262695, 0.42114258, -1.0029297, -0.011238098, 0.37646484, -0.2536621, 0.39916992, -1.6074219, -1.1894531, -0.48535156, -0.8251953, -0.73535156, 0.095581055, -0.21594238, -0.3190918, -0.66748047, 0.76464844, -0.0051116943, -0.12438965, -0.13549805, -0.20092773, -0.33276367, 0.9790039, -0.83984375, 0.69970703, -0.21484375, -0.8876953, -0.25561523, 0.3659668, 0.1697998, -0.73828125, 0.39746094, -0.3918457, -0.037200928, 0.10296631, -0.8359375, -0.71875, -0.7285156, 1.2695312, 0.24169922, 0.32861328, 0.05883789, -0.23046875, -0.44604492, -0.96972656, -1.0097656, -0.32373047, 0.73828125, 0.51904297, 0.3774414, -0.24853516, -0.74316406, 0.13586426, 0.8696289, -0.5605469, -0.55126953, 0.9741211, 0.11126709, -0.25170898, -0.8330078, -0.6621094, 0.26098633, -0.38354492, 0.003627777, 0.39111328, -0.29736328, -0.2487793, -1.3378906, -1.0195312, -0.7680664, -0.97558594, -0.5107422, 1.0273438, 0.40039062, 0.4975586, -0.64404297, 0.8071289, -0.24450684, -0.265625, -0.095336914, 0.37768555, 0.8564453, -0.29785156, -0.21765137, -0.7651367, 0.4543457, -1.0996094, -0.15808105, -1.1318359, -0.67333984, -1.2080078, -0.014701843, -0.19250488, 0.49169922, -0.5185547, 0.36376953, 0.006164551, -0.44384766, -0.8725586, -0.036346436, 0.6035156, -0.31884766, 0.56933594, -0.22607422, -0.16186523, -0.8964844, 0.3503418, -0.0758667, 0.13208008, 

## Task 4: Create a Delta table to store the computed embeddings

Finally, create a Delta table to store the computed embeddings.

Steps:

  1. Define the schema for the Delta table.

  2. Save the DataFrame containing the computed embeddings as a Delta table.


**Note:** Ensure that the Delta table is properly structured to facilitate efficient querying and retrieval of the embeddings.

**📌 Instructions:** 

- Please execute the following SQL code block to create the Delta table. This table will store the computed embeddings along with other relevant information. 

**Important:** Storing the computed embeddings in a structured format like a Delta table ensures efficient querying and retrieval of the embeddings when needed for various downstream tasks such as retrieval-augmented generation. Additionally, setting the `delta.enableChangeDataFeed` property to true enables Change Data Feed (CDC), which is required for VectorSearch to efficiently process changes in the Delta table.

In [0]:
%sql
CREATE TABLE IF NOT EXISTS lab_pdf_text_embeddings (
  id BIGINT GENERATED BY DEFAULT AS IDENTITY,
  pdf_name STRING,
  content STRING,
  embedding ARRAY <FLOAT>
  ---- NOTE: the table has to be CDC because VectorSearch is using DLT that is requiring CDC state
  ) TBLPROPERTIES (delta.enableChangeDataFeed = true);

In [0]:
## define the schema for the Delta table
embedding_table_name = f"{DA.catalog_name}.{DA.schema_name}.lab_pdf_text_embeddings"
## save the DataFrame as a Delta table
df_chunk_emd.write.mode("append").saveAsTable(embedding_table_name)


## Clean up Classroom

**🚨 Warning:** Please refrain from deleting tables created in this lab, as they are required for upcoming labs. To clean up the classroom assets, execute the classroom clean-up script provided in the final lab.


## Conclusion

In this lab, you learned how to prepare data for Retrieval-Augmented Generation (RAG) applications. By extracting text from PDF documents, computing embeddings, and storing them in a Delta table, you can enhance the capabilities of language models to generate more accurate and relevant responses.


&copy; 2025 Databricks, Inc. All rights reserved. Apache, Apache Spark, Spark, the Spark Logo, Apache Iceberg, Iceberg, and the Apache Iceberg logo are trademarks of the <a href="https://www.apache.org/" target="blank">Apache Software Foundation</a>.<br/>
<br/><a href="https://databricks.com/privacy-policy" target="blank">Privacy Policy</a> | 
<a href="https://databricks.com/terms-of-use" target="blank">Terms of Use</a> | 
<a href="https://help.databricks.com/" target="blank">Support</a>